In [ ]:
import os 
from glob import glob 
import pandas as pd
import numpy as np

from PIL import Image, ImageColor
import matplotlib.pyplot as plt

import torch

from backend.disentangle_concepts import *
import dnnlib 
import legacy
from backend.color_annotations import *


%load_ext autoreload
%autoreload 2

In [ ]:
images_textiles = glob('/Users/ludovicaschaerf/Desktop/TextAIles/TextileGAN/Original Textiles/*')

In [ ]:
images = []

for step in [10, 20]:
    imh = np.zeros((200, 200))
    imv = np.zeros((200, 200))
    imb = np.ones((200, 200))
    imb2 = np.ones((200, 200))
    
    for x,y in zip(range(0,200, step*2),range(step, 200, step*2)):
        imh[x:y, :] = 255
        imv[:, x:y] = 255
        imb[x:y, :] = 0
        imb[:, x:y] = 0
        imb2[x:y, :] = 0
        imb2[:, x*2:y*2] = 0
    
    images.append(imh)        
    images.append(imb)        
    images.append(imb2)        
    images.append(imv)        

for im in images:
    plt.imshow(im, cmap='gray')
    plt.title('Original Image')
    plt.show()

In [ ]:
def get_freqs(image):
    
    # Load the image
    # image = cv2.imread(image, cv2.IMREAD_GRAYSCALE)
    # Center crop the image to remove black borders
    height, width = image.shape
    short_side = min(height, width)
    crop_size = min(200, short_side)
    center_x = width // 2
    center_y = height // 2
    crop_half_size = crop_size // 2
    image = image[center_y - crop_half_size:center_y + crop_half_size,
                        center_x - crop_half_size:center_x + crop_half_size]

    # kernel = np.ones((5,5), np.float32) / 25
    # image = cv2.filter2D( image, -1, kernel)
    # image = cv2.GaussianBlur(image,(5,5),0)
    # image = image - cv2.GaussianBlur(image, (21, 21), 1) + 127

    # print(np.unique(image))
    # Perform 1D Fourier Transforms
    horizontal_freq = np.fft.fftshift(np.fft.fft(image, axis=1))
    vertical_freq = np.fft.fftshift(np.fft.fft(image, axis=0))
    twod = np.fft.fftshift(np.fft.fft2(image))
    
    # Calculate corresponding frequencies
    num_cols = image.shape[1]
    num_rows = image.shape[0]
    # horizontal_freqs = np.fft.fftshift(np.fft.fftfreq(num_cols))
    # vertical_freqs = np.fft.fftshift(np.fft.fftfreq(num_rows))
    
    horizontal_freqs = np.fft.fftfreq(num_cols)
    vertical_freqs = np.fft.fftfreq(num_rows)
    
    # # Sum power along the second axis
    # twod = twod.real*twod.real + twod.imag*twod.imag
    # twod = twod.sum(axis=1)/twod.shape[1]

    # # Round up the size along this axis to an even number
    # n = int(math.ceil(image.shape[0] / 2.) * 2 )

    # # Generate a list of frequencies
    # f = np.fft.fftfreq(n)

    # # Graph it
    # plt.plot(f[1:],a[1:], label = 'sum of amplitudes over y vs f_x')

    

    # Calculate magnitude spectra
    horizontal_magnitudes = np.abs(horizontal_freq)[0]
    vertical_magnitudes = np.abs(vertical_freq)[0]
    
    # # Find peaks in the magnitudes
    # horizontal_peaks, _ = find_peaks(horizontal_magnitudes, height=100)  # Adjust height threshold as needed
    # vertical_peaks, _ = find_peaks(vertical_magnitudes, height=10)      # Adjust height threshold as needed

    print('Median horizontal frequency', np.median(horizontal_magnitudes), ', median vertical frequency', np.median(vertical_magnitudes))
    # Plot frequency analysis with peaks
    plt.figure(figsize=(25, 5))

    # Plot frequency analysis
    plt.subplot(1, 6, 1)
    plt.imshow(image, cmap='gray')
    plt.title('Original Image')

    plt.subplot(1, 6, 2)
    plt.imshow(np.log(1 + np.abs(horizontal_freq)), cmap='gray')
    plt.title('Horizontal Frequency Analysis')

    plt.subplot(1, 6, 3)
    plt.imshow(np.log(1 + np.abs(vertical_freq)), cmap='gray')
    plt.title('Vertical Frequency Analysis')

    plt.subplot(1, 6, 4)
    plt.imshow(np.log(1 + np.abs(twod)), cmap='gray')
    plt.title('2D Frequency Analysis')

    plt.subplot(1, 6, 5)
    plt.scatter(horizontal_freqs[1:], horizontal_magnitudes[1:], s=5)
    # plt.plot(horizontal_freqs[horizontal_peaks], horizontal_magnitudes[horizontal_peaks], 'ro', markersize=5)
    plt.xlabel('Horizontal Frequency')
    plt.ylabel('Magnitude')
    plt.title('Horizontal Frequency Analysis with Peaks')

    plt.subplot(1, 6, 6)
    plt.scatter(vertical_freqs[1:], vertical_magnitudes[1:], s=5)
    # plt.plot(vertical_freqs[vertical_peaks], vertical_magnitudes[vertical_peaks], 'ro', markersize=5)
    plt.xlabel('Vertical Frequency')
    plt.ylabel('Magnitude')
    plt.title('Vertical Frequency Analysis with Peaks')


    plt.show()


When the absolute value of the frequency is high in the context of Fourier analysis, it indicates the presence of a rapidly changing or repeating pattern in the image. The frequency component's absolute value reflects how many cycles of the pattern occur within a fixed interval.

In Fourier analysis:

Higher Frequency Components: Higher absolute frequency values correspond to faster changes or repetitions in the image data. This means that the pattern or feature represented by that frequency component oscillates more rapidly across the image.

Spatial Frequency: In image analysis, frequency is often associated with how quickly the intensity or color changes as you move across the image. High absolute frequency values indicate rapid changes or transitions in the image content.

Fine Details and Textures: Rapidly oscillating frequency components are associated with fine details and textures in the image. For example, in textiles, high-frequency components might capture the intricate weave patterns or small-scale textures.

Small-Scale Features: Patterns that repeat at small scales, such as fine lines or tiny structures, tend to result in high-frequency components with high absolute values.

Edges and Transitions: Edges and sharp transitions between different colors or intensities are also associated with high-frequency components. These transitions involve rapid changes in intensity, leading to higher absolute frequency values.

In [ ]:
import cv2
from scipy.signal import find_peaks

import numpy as np
import matplotlib.pyplot as plt


for image in images:
    get_freqs(image)

In [ ]:
import cv2
import numpy as np
import matplotlib.pyplot as plt
from scipy.signal import find_peaks
from collections import Counter
import seaborn as sns
# Load the image
image = cv2.imread(images_textiles[0], cv2.IMREAD_GRAYSCALE)

# Perform 1D Fourier Transforms
horizontal_freq = np.fft.fftshift(np.fft.fft(image, axis=1))
vertical_freq = np.fft.fftshift(np.fft.fft(image, axis=0))

# Calculate magnitude spectra
horizontal_magnitudes = np.abs(horizontal_freq)[0]
vertical_magnitudes = np.abs(vertical_freq)[0]

# Create histograms of magnitude recurrence
horizontal_magnitude_counter = Counter(np.round(horizontal_magnitudes).astype(int))
vertical_magnitude_counter = Counter(np.round(vertical_magnitudes).astype(int))

# Plot magnitude recurrence histograms
plt.figure(figsize=(12, 5))

plt.subplot(1, 2, 1)
sns.histplot(list(horizontal_magnitude_counter.elements()), kde=True, color='blue')
plt.xlim(0, 1000)  # Limit x-axis range
plt.xlabel('Magnitude')
plt.ylabel('Recurrence')
plt.title('Horizontal Magnitude Recurrence')

plt.subplot(1, 2, 2)
sns.histplot(list(vertical_magnitude_counter.elements()), kde=True, color='green')
plt.xlim(0, 1000)  # Limit x-axis range
plt.xlabel('Magnitude')
plt.ylabel('Recurrence')
plt.title('Vertical Magnitude Recurrence')

plt.tight_layout()
plt.show()


In [ ]:
import cv2
import numpy as np
import matplotlib.pyplot as plt
from skimage.feature import hog
from skimage import exposure

# Load the image
image = cv2.imread(images_textiles[4], cv2.IMREAD_GRAYSCALE)

# Center crop the image to remove black borders
height, width = image.shape
crop_size = 200
center_x = width // 2
center_y = height // 2
crop_half_size = crop_size // 2
cropped_image = image[center_y - crop_half_size:center_y + crop_half_size,
                      center_x - crop_half_size:center_x + crop_half_size]

# Compute HOG features
orientations = 9
pixels_per_cell = (5, 5)
cells_per_block = (1,1)
hog_features, hog_image = hog(cropped_image, orientations=orientations,
                              pixels_per_cell=pixels_per_cell,
                              cells_per_block=cells_per_block,
                              block_norm='L2-Hys',
                              visualize=True)

# Plot the HOG image
plt.figure(figsize=(8, 4))
plt.subplot(1, 2, 1)
plt.imshow(cropped_image, cmap='gray')
plt.title('Original Image')

plt.subplot(1, 2, 2)
plt.imshow(hog_image, cmap='gray')
plt.title('HOG Image')
plt.axis('off')

plt.tight_layout()
plt.show()

# Plot the orientation distribution
hog_histogram, _ = np.histogram(hog_features, bins=orientations)
angles_deg = np.arange(0, 180, 180/orientations)
plt.figure(figsize=(6, 4))
plt.bar(angles_deg, hog_histogram, width=180/orientations)
plt.xlabel('Orientation (degrees)')
plt.ylabel('Frequency')
plt.title('Orientation Distribution')
plt.xticks(angles_deg)
plt.show()

In [ ]:
import cv2
import numpy as np
import matplotlib.pyplot as plt
import pywt

# Load the image
image = cv2.imread(images_textiles[0], cv2.IMREAD_GRAYSCALE)

# Perform Continuous Wavelet Transform (CWT) on each row of the image
wavelet = 'morl'  # You can choose a different wavelet basis
scales = np.arange(1, 20)  # Scales to analyze

cwt_coeffs = []
for row in image:
    coeffs, _ = pywt.cwt(row, scales, wavelet)
    cwt_coeffs.append(coeffs)

cwt_coeffs = np.array(cwt_coeffs)

# Plot scaleograms
plt.figure(figsize=(10, 6))
plt.imshow(np.abs(cwt_coeffs[:, 0, :]), extent=[0, image.shape[1], scales[-1], scales[0]], cmap='viridis', aspect='auto')
plt.colorbar(label='Magnitude')
plt.title('Wavelet Scaleogram')
plt.xlabel('Pixel')
plt.ylabel('Scale')
plt.show()
